# Run pre-trained DeepSeek Coder 1.3B Model on Chat-GPT 4o generated dataset

In [31]:
import pandas as pd 
import warnings
warnings.filterwarnings("ignore")
from transformers import AutoTokenizer, AutoModelForCausalLM
import torch
import sys
import os
import sqlite3 as sql
from huggingface_hub import snapshot_download

In [32]:
is_google_colab=False

In [ ]:
current_path = "./"

def get_path(rel_path):
    return os.path.join(current_path, rel_path)

if is_google_colab:
    hugging_face_path = snapshot_download(
        repo_id="USC-Applied-NLP-Group/SQL-Generation",
        repo_type="model",  
        allow_patterns=["src/*", "train-data/*", "deepseek-coder-1.3b-instruct/*", "nba-data/*"], 
    )
    sys.path.append(hugging_face_path)
    current_path = hugging_face_path

In [34]:
from src.prompts.prompt import input_text
from src.evaluation.compare_result import compare_result

## First load dataset into pandas dataframe

In [ ]:
# Load dataset and check length
df = pd.read_csv(get_path("train-data/sql_train.tsv"), sep="\t")
print("Total dataset examples: " + str(len(df)))
print("\n")

# Test sampling
sample = df.sample(n=1)
print(sample["natural_query"].values[0])
print(sample["sql_query"].values[0])
print(sample["result"].values[0])

Total dataset examples: 1044


How many points did the Phoenix Suns score in the highest scoring away game they played?
SELECT MAX(pts_away) FROM game WHERE team_abbreviation_away = 'PHX';
161.0


## Load pre-trained DeepSeek model using transformers and pytorch packages

In [ ]:
# Set device to cuda if available, otherwise CPU
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")

# Load model and tokenizer
tokenizer = AutoTokenizer.from_pretrained(get_path("deepseek-coder-1.3b-instruct"))
model = AutoModelForCausalLM.from_pretrained(get_path("deepseek-coder-1.3b-instruct"), torch_dtype=torch.bfloat16, device_map=device) 
model.generation_config.pad_token_id = tokenizer.pad_token_id

## Test model performance on a single example

In [28]:
# Create message with sample query and run model
message=[{ 'role': 'user', 'content': input_text + sample["natural_query"].values[0]}]
inputs = tokenizer.apply_chat_template(message, add_generation_prompt=True, return_tensors="pt").to(model.device)
outputs = model.generate(inputs, max_new_tokens=512, do_sample=False, top_k=50, top_p=0.95, num_return_sequences=1, eos_token_id=tokenizer.eos_token_id)

# Print output
query_output = tokenizer.decode(outputs[0][len(inputs[0]):], skip_special_tokens=True)
print(query_output)

SQLite:
SELECT team_abbreviation_home FROM other_stats WHERE lead_changes = 1 AND season_id = '2001';



# Test sample output on sqlite3 database

In [ ]:
# Create connection to sqlite3 database
connection = sql.connect(get_path('nba-data/nba.sqlite'))
cursor = connection.cursor()

# Execute query from model output and print result
if query_output[0:7] == "SQLite:":
    print("cleaned")
    query = query_output[7:]
elif query_output[0:4] == "SQL:":
    query = query_output[4:]
else:
    query = query_output

try:
    cursor.execute(query)
    rows = cursor.fetchall()
    for row in rows:
        print(row)
except:
    pass

cleaned


## Create function to compare output to ground truth result from examples

In [12]:
# Obtain sample
sample = df.sample(n=1)

print(sample["natural_query"].values[0])
print(sample["sql_query"].values[0])
print(sample["result"].values[0])

# Create message with sample query and run model
message=[{ 'role': 'user', 'content': input_text + sample["natural_query"].values[0]}]
inputs = tokenizer.apply_chat_template(message, add_generation_prompt=True, return_tensors="pt").to(model.device)
outputs = model.generate(inputs, max_new_tokens=512, do_sample=False, top_k=50, top_p=0.95, num_return_sequences=1, eos_token_id=tokenizer.eos_token_id)

# Print output
query_output = tokenizer.decode(outputs[0][len(inputs[0]):], skip_special_tokens=True)
print(query_output)

result = compare_result(cursor, sample["sql_query"].values[0], sample["result"].values[0], query_output)
print("Statement valid? " + str(result[0]))
print("SQLite matched? " + str(result[1]))
print("Result matched? " + str(result[2]))

ImportError: cannot import name 'compare_result_two' from 'src.evaluation.compare_result' (/Users/esteban/Documents/USC/spring_2025/NLP/SQL-Generation/src/evaluation/compare_result.py)

## Create function to evaluate pretrained model on full datasets

In [ ]:
def run_evaluation(nba_df, title):
    counter = 0
    num_valid = 0
    num_sql_matched = 0
    num_result_matched = 0
    for index, row in nba_df.iterrows():
        # Create message with sample query and run model
        message=[{ 'role': 'user', 'content': input_text + row["natural_query"]}]
        inputs = tokenizer.apply_chat_template(message, add_generation_prompt=True, return_tensors="pt").to(model.device)
        outputs = model.generate(inputs, max_new_tokens=512, do_sample=False, top_k=50, top_p=0.95, num_return_sequences=1, eos_token_id=tokenizer.eos_token_id)

        # Obtain output
        query_output = tokenizer.decode(outputs[0][len(inputs[0]):], skip_special_tokens=True)

        # Evaluate model result
        valid, sql_matched, result_matched = compare_result(cursor, row["sql_query"], row["result"], query_output)
        if valid:
            num_valid += 1
        if sql_matched:
            num_sql_matched += 1
        if result_matched:
            num_result_matched += 1

        # Break after predefined number of examples
        counter += 1
        if counter % 50 == 0:
            print("Completed " + str(counter))

    # Print evaluation results
    print("\n" + title + " results:")
    print("Percent valid: " + str(num_valid / len(nba_df)))
    print("Percent SQLite matched: " + str(num_sql_matched / len(nba_df)))
    print("Percent result matched: " + str(num_result_matched / len(nba_df)))

# Evaluate on less than 90 dataset

In [ ]:
less_than_90_df = pd.read_csv(get_path("train-data/less_than_90.tsv"), sep='\t')
run_evaluation(less_than_90_df, "Less than 90")
print("Dataset length: " + str(len(less_than_90_df)))

Completed 50
Completed 100
Completed 150
Completed 200

Less than 90 results:
Percent valid: 0.8448979591836735
Percent SQLite matched: 0.43673469387755104
Percent result matched: 0.6530612244897959
Dataset length: 245


# Evaluate on game table queries

In [ ]:
game_queries = pd.read_csv(get_path("train-data/queries_from_game.tsv"), sep='\t')
run_evaluation(game_queries, "Queries from game")
print("Dataset length: " + str(len(game_queries)))

Completed 50
Completed 100
Completed 150
Completed 200
Completed 250
Completed 300
Completed 350
Completed 400
Completed 450
Completed 500
Completed 550
Completed 600
Completed 650
Completed 700
Completed 750
Completed 800

Queries from game results:
Percent valid: 0.7613365155131265
Percent SQLite matched: 0.13842482100238662
Percent result matched: 0.383054892601432
Dataset length: 838


## Evaluate on other stats queries

In [ ]:
other_stats_queries = pd.read_csv(get_path("train-data/queries_from_other_stats.tsv"), sep='\t')
run_evaluation(other_stats_queries, "Queries from other stats")
print("Dataset length: " + str(len(other_stats_queries)))

Completed 50
Completed 100
Completed 150

Queries from other stats results:
Percent valid: 0.21428571428571427
Percent SQLite matched: 0.01948051948051948
Percent result matched: 0.07142857142857142
Dataset length: 154


## Evaluate on team queries

In [ ]:
team_queries = pd.read_csv(get_path("train-data/queries_from_team.tsv"), sep='\t')
run_evaluation(team_queries, "Queries from team")
print("Dataset length: " + str(len(team_queries)))

Completed 50

Queries from team results:
Percent valid: 0.8653846153846154
Percent SQLite matched: 0.5961538461538461
Percent result matched: 0.7884615384615384
Dataset length: 52


## Evaluate on queries requiring join statements

In [ ]:
join_queries = pd.read_csv(get_path("train-data/with_join.tsv"), sep='\t')
run_evaluation(join_queries, "Queries with join")
print("Dataset length: " + str(len(join_queries)))

Completed 50
Completed 100
Completed 150

Queries with join results:
Percent valid: 0.1945945945945946
Percent SQLite matched: 0.0
Percent result matched: 0.04864864864864865
Dataset length: 185


## Evaluate on queries not requiring join statements

In [ ]:
no_join_queries = pd.read_csv(get_path("train-data/without_join.tsv"), sep='\t')
run_evaluation(no_join_queries, "Queries without join")
print("Dataset length: " + str(len(no_join_queries)))

Completed 50
Completed 100
Completed 150
Completed 200
Completed 250
Completed 300
Completed 350
Completed 400
Completed 450
Completed 500
Completed 550
Completed 600
Completed 650
Completed 700
Completed 750
Completed 800
Completed 850

Queries without join results:
Percent valid: 0.7916181606519208
Percent SQLite matched: 0.17462165308498254
Percent result matched: 0.42374854481955765
Dataset length: 859


## Evaluate on full training dataset

In [15]:
# Run evaluation on all training data
run_evaluation(df, "All training data")
print("Dataset length: " + str(len(df)))

Completed 50
Completed 100
Completed 150
Completed 200
Completed 250
Completed 300
Completed 350
Completed 400
Completed 450
Completed 500
Completed 550
Completed 600
Completed 650
Completed 700
Completed 750
Completed 800
Completed 850
Completed 900
Completed 950
Completed 1000

All training data results:
Percent valid: 0.685823754789272
Percent SQLite matched: 0.14367816091954022
Percent result matched: 0.35823754789272033
Dataset length: 1044
